In [16]:
from neo4j import GraphDatabase
from tabulate import tabulate
URI = "neo4j://localhost:7687" 
USERNAME = "neo4j"
PASSWORD = "password"

In [17]:
def execute_query(query, params=None):
    """Execute a Cypher query and return results."""
    with GraphDatabase.driver(URI, auth=(USERNAME, PASSWORD)) as driver:
        with driver.session() as session:
            result = session.run(query, params or {})
            return [record.data() for record in result]

In [25]:
def print_table(data):
    if data:
        print(tabulate(data, headers="keys", tablefmt="grid"))

In [26]:
# Get 10 hospitals and the list of specializations they provide
query1 = """MATCH (h:Hospital)<-[:WORKS_AT]-(p:Provider)-[:SPECIALIZES_IN]->(t:Taxonomy)
RETURN h.FacilityName AS Hospital,
COLLECT(DISTINCT t.Description) AS Specializations,
COLLECT(DISTINCT p.FirstName) AS Providers
LIMIT 10;"""
print(execute_query(query1))


Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.UnknownRelationshipTypeWarning} {category: UNRECOGNIZED} {title: The provided relationship type is not in the database.} {description: One of the relationship types in your query is not available in the database, make sure you didn't misspell it or that the label is available when you run this statement in your application (the missing relationship type is: SPECIALIZES_IN)} {position: line: 1, column: 48, offset: 47} for query: 'MATCH (h:Hospital)<-[:WORKS_AT]-(p:Provider)-[:SPECIALIZES_IN]->(t:Taxonomy)\nRETURN h.FacilityName AS Hospital,\nCOLLECT(DISTINCT t.Description) AS Specializations,\nCOLLECT(DISTINCT p.FirstName) AS Providers\nLIMIT 10;'


[]


In [27]:
# Get the hospital and its count with the maximum number of specialties offered
query2 = """MATCH (h:Hospital)<-[:WORKS_AT]-(p:Provider)-[:SPECIALIZES_IN]->(t:Taxonomy)
RETURN h.FacilityName AS Hospital, COUNT(DISTINCT t) AS SpecializationCount
ORDER BY SpecializationCount DESC
LIMIT 1;"""
print(execute_query(query2))


Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.UnknownRelationshipTypeWarning} {category: UNRECOGNIZED} {title: The provided relationship type is not in the database.} {description: One of the relationship types in your query is not available in the database, make sure you didn't misspell it or that the label is available when you run this statement in your application (the missing relationship type is: SPECIALIZES_IN)} {position: line: 1, column: 48, offset: 47} for query: 'MATCH (h:Hospital)<-[:WORKS_AT]-(p:Provider)-[:SPECIALIZES_IN]->(t:Taxonomy)\nRETURN h.FacilityName AS Hospital, COUNT(DISTINCT t) AS SpecializationCount\nORDER BY SpecializationCount DESC\nLIMIT 1;'


[]


In [28]:
# Given a city and specialty, get the facility name and the number of providers that specialize in it
query3 = """MATCH (c:City {name: 'SAN FRANCISCO'})<-[:IN_CITY]-(h:Hospital)
MATCH (h)<-[:WORKS_AT]-(p:Provider)-[:SPECIALIZES_IN]->(t:Taxonomy)
WHERE t.Description = 'Physician Assistants & Advanced Practice Nursing Providers/Nurse Practitioner, Acute Care'
RETURN h.FacilityName, COUNT(p) AS provider_count
ORDER BY provider_count DESC;"""
print(execute_query(query3))

Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.UnknownRelationshipTypeWarning} {category: UNRECOGNIZED} {title: The provided relationship type is not in the database.} {description: One of the relationship types in your query is not available in the database, make sure you didn't misspell it or that the label is available when you run this statement in your application (the missing relationship type is: IN_CITY)} {position: line: 1, column: 43, offset: 42} for query: "MATCH (c:City {name: 'SAN FRANCISCO'})<-[:IN_CITY]-(h:Hospital)\nMATCH (h)<-[:WORKS_AT]-(p:Provider)-[:SPECIALIZES_IN]->(t:Taxonomy)\nWHERE t.Description = 'Physician Assistants & Advanced Practice Nursing Providers/Nurse Practitioner, Acute Care'\nRETURN h.FacilityName, COUNT(p) AS provider_count\nORDER BY provider_count DESC;"
Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.UnknownLabelWarning} {category: UNRECOGNIZE

[]


In [29]:
# Connection between 2 hospitals
query4 = """MATCH p=shortestPath((h1:Hospital {FacilityName: 'HOLT MEDICAL CENTER'})-[:WORKS_AT|SPECIALIZES_IN*]-(h2:Hospital {FacilityName: 'ANZA COMMUNITY HEALTH'}))
RETURN p;"""
print(execute_query(query4))


Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.UnknownRelationshipTypeWarning} {category: UNRECOGNIZED} {title: The provided relationship type is not in the database.} {description: One of the relationship types in your query is not available in the database, make sure you didn't misspell it or that the label is available when you run this statement in your application (the missing relationship type is: SPECIALIZES_IN)} {position: line: 1, column: 85, offset: 84} for query: "MATCH p=shortestPath((h1:Hospital {FacilityName: 'HOLT MEDICAL CENTER'})-[:WORKS_AT|SPECIALIZES_IN*]-(h2:Hospital {FacilityName: 'ANZA COMMUNITY HEALTH'}))\nRETURN p;"


[]


In [30]:
# Gets the path connecting a hospital to a specialty; can find the closest hospital based on that specialty in relationships

query5 = """MATCH p=shortestPath((h1:Hospital {FacilityName: 'HOLT MEDICAL CENTER'})-[:WORKS_AT|SPECIALIZES_IN*]-(t:Taxonomy {Description: 'Physician Assistants & Advanced Practice Nursing Providers/Nurse Practitioner, Acute Care'}))
RETURN p;"""

print(execute_query(query5))

Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.UnknownRelationshipTypeWarning} {category: UNRECOGNIZED} {title: The provided relationship type is not in the database.} {description: One of the relationship types in your query is not available in the database, make sure you didn't misspell it or that the label is available when you run this statement in your application (the missing relationship type is: SPECIALIZES_IN)} {position: line: 1, column: 85, offset: 84} for query: "MATCH p=shortestPath((h1:Hospital {FacilityName: 'HOLT MEDICAL CENTER'})-[:WORKS_AT|SPECIALIZES_IN*]-(t:Taxonomy {Description: 'Physician Assistants & Advanced Practice Nursing Providers/Nurse Practitioner, Acute Care'}))\nRETURN p;"


[]


In [20]:
# Hospital with the most number of doctors
query6 = """MATCH (h:Hospital)<-[:WORKS_AT]-(p:Provider)
WITH h, COUNT(p) AS providerCount
RETURN h.FacilityName AS hospitalName, providerCount
ORDER BY providerCount DESC;"""
result = execute_query(query6)
print_table(result)

+--------------------------------------------------------------+-----------------+
| hospitalName                                                 |   providerCount |
+==============================================================+=================+
| MAXIM HEALTHCARE SERVICES HOLDINGS INC                       |            4039 |
+--------------------------------------------------------------+-----------------+
| UCSF MEDICAL CTR                                             |            3153 |
+--------------------------------------------------------------+-----------------+
| BEHAVIORAL HEALTH WORKS                                      |            2462 |
+--------------------------------------------------------------+-----------------+
| LOS ANGELES MEDICAL CENTER-LAL                               |            2037 |
+--------------------------------------------------------------+-----------------+
| OC ANAHEIM MEDICAL CENTER-OCAL                               |            1645 |
+---

In [19]:
#  The most connected doctor -> works in multiple locations
query7 = """MATCH (p:Provider)-[:WORKS_AT]->(h:Hospital)
WITH p.FirstName + ' ' + p.LastName AS providerName,
COLLECT(DISTINCT h) AS hospitals,
COUNT(DISTINCT h) AS hospitalCount
RETURN providerName, hospitalCount,
[hospital IN hospitals | hospital.FacilityName] AS hospitalNames
ORDER BY hospitalCount DESC;"""
result = execute_query(query7)
print_table(result)

+-------------------------------------+-----------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
| providerName                        |   hospitalCount | hospitalNames                                                                                                                                                                                                                       |
+=====================================+=================+=====================================================================================================================================================================================================================================+
| FIDEL SANTACRUZ                     |               6 | ['LOS ANGELES COMMUNITY HOSPITAL', 'ST. FRANCIS MEDICAL CENTER', 'MONTEREY PAR

In [21]:
# Hospital with the most insurances covered; or most covered insurance
query8 = """MATCH (h:Hospital)<-[:WORKS_AT]-(p:Provider)-[:PART_OF]->(sn:SubNetwork)-[:UNDER]->(mcp:ManagedCarePlan)
WITH h, COLLECT(DISTINCT mcp) AS managedCarePlans
WITH h, managedCarePlans, SIZE(managedCarePlans) AS planCount
RETURN h.FacilityName AS hospitalName, planCount, [mcp IN managedCarePlans | mcp.name] AS managedCarePlanNames
ORDER BY planCount DESC;"""
result = execute_query(query8)
print_table(result)

+--------------------------------------------------------------+-------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
| hospitalName                                                 |   planCount | managedCarePlanNames                                                                                                                                                                                                                                           |
+==============================================================+=============+==========================================================================================================================================================================================================================================================

In [23]:
query9 = """MATCH (p1:Provider)-[:HAS_TAXONOMY]->(t:Taxonomy)<-[:HAS_TAXONOMY]-(p2:Provider)
WHERE p1.FirstName + " " + p1.LastName < p2.FirstName + " " + p2.LastName
WITH p1.FirstName + " " + p1.LastName AS Doctor1,
     p2.FirstName + " " + p2.LastName AS Doctor2,
     t.Description AS SharedSpecialty
WITH DISTINCT Doctor1, Doctor2, SharedSpecialty
LIMIT 100
RETURN Doctor1, Doctor2, SharedSpecialty
ORDER BY Doctor1, Doctor2;"""
result = execute_query(query9)
print_table(result)


+---------------------------+---------------------------+------------------------------------------------------+
| Doctor1                   | Doctor2                   | SharedSpecialty                                      |
+===========================+===========================+======================================================+
| Azra Zarrinpar            | JONATHAN LYNNE            | Allopathic & Osteopathic Physicians/General Practice |
+---------------------------+---------------------------+------------------------------------------------------+
| Azra Zarrinpar            | PETIA KREMEN              | Allopathic & Osteopathic Physicians/General Practice |
+---------------------------+---------------------------+------------------------------------------------------+
| Azra Zarrinpar            | SHAHRZAD SODAGAR-MARVASTI | Allopathic & Osteopathic Physicians/General Practice |
+---------------------------+---------------------------+---------------------------------------